## Poorly cleaned and documented notebook for evaluating text generation with BLEU and BERTScore

In [1]:
from datasets import load_dataset, concatenate_datasets
import transformers
from transformers import (
    Trainer,
    TrainingArguments,
    default_data_collator,
    AutoModelForCausalLM,
    AutoModelForSequenceClassification,
    PreTrainedTokenizerFast,
    AutoModelWithLMHead,
    AutoConfig,
    AutoModel,
    AutoTokenizer,
    GPT2TokenizerFast,
    GPT2Config
)
import datasets
import torch
import numpy as np
import os
from tokenizers.processors import TemplateProcessing

from evaluate import load

"""
model_type = "custom"
if model_type == "large":
    tokenizer = AutoTokenizer.from_pretrained("H:\\Data_temp\\checkpoints\\large\\checkpoint-12200")
    model = AutoModelForCausalLM.from_pretrained("H:\\Data_temp\\checkpoints\\large\\checkpoint-12200").to("cuda")
elif model_type == "small":
    tokenizer = AutoTokenizer.from_pretrained(r"H:\Data_temp\checkpoints\small\checkpoint-140000")
    model = AutoModelForCausalLM.from_pretrained(r"H:\Data_temp\checkpoints\small\checkpoint-140000").to("cuda")
elif model_type == "custom":
    tokenizer = GPT2TokenizerFast.from_pretrained('Finnish-NLP/gpt2-large-finnish')
    model = AutoModelForCausalLM.from_pretrained('Finnish-NLP/gpt2-large-finnish').to("cuda")
elif model_type == "distill":
    config = GPT2Config.from_pretrained(r"H:\Data_temp\checkpoints\distillation\third\config.json")
    tokenizer = AutoTokenizer.from_pretrained(r"H:\Data_temp\checkpoints\large\checkpoint-12200")
    model = AutoModelForCausalLM.from_pretrained(r"H:\Data_temp\checkpoints\distillation\third\model_step_640000.pth",config=config).to("cuda")
"""
bleu = load("bleu")
bertscore = load("bertscore")

In [2]:
#input_dir = "H:\\Data_temp\\1024_bpe_dataset2"
#dataset = datasets.load_from_disk(input_dir)["test"]
#dataset
dataset = datasets.load_dataset("Finnish-NLP/mc4_fi_cleaned", split="validation").remove_columns(["timestamp","url"])
dataset = dataset.filter(lambda e: len(e["text"]) > 200, num_proc=12, load_from_cache_file=False, writer_batch_size=100000)
dataset

Using custom data configuration Finnish-NLP--mc4_fi_cleaned-c578f3a358717f8c
Reusing dataset csv (H:\Data_temp\cache\Finnish-NLP___csv\Finnish-NLP--mc4_fi_cleaned-c578f3a358717f8c\0.0.0\652c3096f041ee27b04d2232d41f10547a8fecda3e284a79a0ec4053c916ef7a)


Dataset({
    features: ['text', 'perplexity_kenlm_full'],
    num_rows: 17877
})

In [3]:

predictions = ["hello there", "general kenobi"]
references = ["hello there", "general kenobi"]
results = bertscore.compute(predictions=predictions, references=references, lang="fi")
results

{'precision': [1.0, 0.9999998807907104],
 'recall': [1.0, 0.9999998807907104],
 'f1': [1.0, 0.9999998807907104],
 'hashcode': 'bert-base-multilingual-cased_L9_no-idf_version=0.3.11(hug_trans=4.15.0)'}

In [3]:


tokenizer = AutoTokenizer.from_pretrained(r"H:\Data_temp\checkpoints\large\checkpoint-31500")
model = AutoModelForCausalLM.from_pretrained(r"H:\Data_temp\checkpoints\large\checkpoint-31500").to("cuda")
refs = []
predictions = []
from tqdm import tqdm
for i in tqdm(range(0,200)):
    input_text = dataset[i]["text"]  
    ids = tokenizer.encode(input_text, add_special_tokens=False, return_tensors="pt").to("cuda")
    generation_len = 50
    if ids.shape[1] < generation_len*2:
        first = ids[:,:(ids.shape[1]//2)]
        second = ids[:,(ids.shape[1]//2):]
    else:
        cutoff = min(300,ids.shape[1]-generation_len)
        first = ids[:,:cutoff]
        second = ids[:,cutoff:cutoff+generation_len]
    #print(tokenizer.decode(,skip_special_tokens=True, clean_up_tokenization_spaces=True))
    text_in = tokenizer.decode(first[0],skip_special_tokens=True, clean_up_tokenization_spaces=True)
    ref = tokenizer.decode(second[0],skip_special_tokens=True, clean_up_tokenization_spaces=True)
    prompt_len = len(text_in)
    model_out = model.generate(first, max_length=first.shape[1]+second.shape[1], do_sample=True, top_p=0.9, top_k=20, temperature=0.9, pad_token_id=tokenizer.eos_token_id)


    text_out = tokenizer.decode(model_out[0],skip_special_tokens=True, clean_up_tokenization_spaces=True)[prompt_len:]
    refs.append([ref])
    predictions.append(text_out)
  
#len(tokenizer.decode(first,skip_special_tokens=True, clean_up_tokenization_spaces=True))
len(refs[:-1]), len(predictions[:-1])
bs = bertscore.compute(predictions=predictions[:-1], references=refs[:-1], lang="fi")
np.mean(bs["precision"]), np.mean(bs["recall"]),np.mean(bs["f1"]),bleu.compute(predictions=predictions, max_order = 3, references=refs)

100%|██████████| 200/200 [06:53<00:00,  2.07s/it]


(0.6634505313245496,
 0.6440643028697776,
 0.6530068675477301,
 {'bleu': 0.055396740403126914,
  'precisions': [0.1908035441490987,
   0.040655531043176804,
   0.022608978529603124],
  'brevity_penalty': 0.9896657459467438,
  'length_ratio': 0.9897187783489567,
  'translation_length': 6546,
  'reference_length': 6614})

In [4]:

tokenizer = GPT2TokenizerFast.from_pretrained('Finnish-NLP/gpt2-large-finnish')
model = AutoModelForCausalLM.from_pretrained('Finnish-NLP/gpt2-large-finnish').to("cuda")
refs = []
predictions = []
from tqdm import tqdm
for i in tqdm(range(0,5000)):
    input_text = dataset[i]["text"]  
    ids = tokenizer.encode(input_text, add_special_tokens=False, return_tensors="pt").to("cuda")
    generation_len = 50
    if ids.shape[1] < generation_len*2:
        first = ids[:,:(ids.shape[1]//2)]
        second = ids[:,(ids.shape[1]//2):]
    else:
        cutoff = min(300,ids.shape[1]-generation_len)
        first = ids[:,:cutoff]
        second = ids[:,cutoff:cutoff+generation_len]
    #print(tokenizer.decode(,skip_special_tokens=True, clean_up_tokenization_spaces=True))
    text_in = tokenizer.decode(first[0],skip_special_tokens=True, clean_up_tokenization_spaces=True)
    ref = tokenizer.decode(second[0],skip_special_tokens=True, clean_up_tokenization_spaces=True)
    prompt_len = len(text_in)
    model_out = model.generate(first, max_length=first.shape[1]+second.shape[1], do_sample=True, top_p=0.9, top_k=20, temperature=0.9, pad_token_id=tokenizer.eos_token_id)


    text_out = tokenizer.decode(model_out[0],skip_special_tokens=True, clean_up_tokenization_spaces=True)[prompt_len:]
    refs.append([ref])
    predictions.append(text_out)
  
#len(tokenizer.decode(first,skip_special_tokens=True, clean_up_tokenization_spaces=True))
len(refs[:-1]), len(predictions[:-1])
bs = bertscore.compute(predictions=predictions[:-1], references=refs[:-1], lang="fi")
np.mean(bs["precision"]), np.mean(bs["recall"]),np.mean(bs["f1"]),bleu.compute(predictions=predictions, max_order = 3, references=refs)

100%|██████████| 5000/5000 [2:07:15<00:00,  1.53s/it]  


(0.6666507967282925,
 0.6589269880879806,
 0.6626176441889043,
 {'bleu': 0.0670418098328639,
  'precisions': [0.20027962065152674,
   0.04913386342784744,
   0.030621010257533138],
  'brevity_penalty': 1.0,
  'length_ratio': 1.0874531748601026,
  'translation_length': 188112,
  'reference_length': 172984})

In [4]:

config = GPT2Config.from_pretrained(r"H:\Data_temp\checkpoints\distillation\third\config.json")
tokenizer = AutoTokenizer.from_pretrained(r"H:\Data_temp\checkpoints\large\checkpoint-12200")
model = AutoModelForCausalLM.from_pretrained(r"H:\Data_temp\checkpoints\distillation\third\model_step_640000.pth",config=config).to("cuda")

refs = []
predictions = []
from tqdm import tqdm
for i in tqdm(range(0,5000)):
    input_text = dataset[i]["text"]  
    ids = tokenizer.encode(input_text, add_special_tokens=False, return_tensors="pt").to("cuda")
    generation_len = 50
    if ids.shape[1] < generation_len*2:
        first = ids[:,:(ids.shape[1]//2)]
        second = ids[:,(ids.shape[1]//2):]
    else:
        cutoff = min(300,ids.shape[1]-generation_len)
        first = ids[:,:cutoff]
        second = ids[:,cutoff:cutoff+generation_len]
    #print(tokenizer.decode(,skip_special_tokens=True, clean_up_tokenization_spaces=True))
    text_in = tokenizer.decode(first[0],skip_special_tokens=True, clean_up_tokenization_spaces=True)
    ref = tokenizer.decode(second[0],skip_special_tokens=True, clean_up_tokenization_spaces=True)
    prompt_len = len(text_in)
    model_out = model.generate(first, max_length=first.shape[1]+second.shape[1], do_sample=True, top_p=0.9, top_k=20, temperature=0.9)

    text_out = tokenizer.decode(model_out[0],skip_special_tokens=True, clean_up_tokenization_spaces=True)[prompt_len:]
    refs.append([ref])
    predictions.append(text_out)

#len(tokenizer.decode(first,skip_special_tokens=True, clean_up_tokenization_spaces=True))
len(refs[:-1]), len(predictions[:-1])

bs = bertscore.compute(predictions=predictions[:-1], references=refs[:-1], lang="fi")
np.mean(bs["precision"]), np.mean(bs["recall"]),np.mean(bs["f1"]),bleu.compute(predictions=predictions, max_order = 3, references=refs)

100%|██████████| 5000/5000 [31:45<00:00,  2.62it/s]


(0.6383409978068096,
 0.6306679480539414,
 0.6342477605781166,
 {'bleu': 0.03856691099017293,
  'precisions': [0.1578578489573254,
   0.026338544827623246,
   0.013797061777723815],
  'brevity_penalty': 1.0,
  'length_ratio': 1.1590775442404109,
  'translation_length': 191191,
  'reference_length': 164951})

(0.6388155258841742,
 0.6306526358722806,
 0.6344889989374256,
 {'bleu': 0.03930537488413642,
  'precisions': [0.15936290453519372,
   0.026434821894379037,
   0.014414255079256295],
  'brevity_penalty': 1.0,
  'length_ratio': 1.1574891937605714,
  'translation_length': 190929,
  'reference_length': 164951})

In [7]:
"small"
bs = bertscore.compute(predictions=predictions[:-1], references=refs[:-1], lang="fi")
np.mean(bs["precision"]), np.mean(bs["recall"]),np.mean(bs["f1"]),bleu.compute(predictions=predictions, max_order = 3, references=refs)

(0.6375111702037444,
 0.6052083602891634,
 0.619867973898525,
 {'bleu': 0.022332107109682052,
  'precisions': [0.16789440254648727,
   0.018320622249823913,
   0.006682495007783141],
  'brevity_penalty': 0.8152510033623226,
  'length_ratio': 0.8303859934162267,
  'translation_length': 136973,
  'reference_length': 164951})

In [8]:
"large"
bs = bertscore.compute(predictions=predictions[:-1], references=refs[:-1], lang="fi")
np.mean(bs["precision"]), np.mean(bs["recall"]),np.mean(bs["f1"]),bleu.compute(predictions=predictions, max_order = 3, references=refs)

(0.6604929250713634,
 0.6431061869670115,
 0.6511941092279964,
 {'bleu': 0.05717298400424163,
  'precisions': [0.19105301467912167,
   0.04063799843627834,
   0.024110462714315224],
  'brevity_penalty': 0.9994481688137139,
  'length_ratio': 0.9994483210165443,
  'translation_length': 164860,
  'reference_length': 164951})

In [11]:
import pickle
with open('preds.pickle', 'wb') as handle:
    pickle.dump(predictions, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('refs.pickle', 'wb') as handle:
    pickle.dump(refs, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [2]:
import pickle
preds_load = None
refs_load = None
with open('preds.pickle', 'rb') as handle:
    preds_load = pickle.load(handle)
with open('refs.pickle', 'rb') as handle:
    refs_load = pickle.load(handle)
bleu_score = bleu.compute(predictions=preds_load, max_order = 4, references=refs_load)
bs = bertscore.compute(predictions=preds_load, references=refs_load, lang="fi")
np.mean(bs["precision"]),np.mean(bs["f1"]), bleu_score

(0.6159351132384818,
 {'bleu': 0.034312445993591324,
  'precisions': [0.2048581077785663,
   0.03431786300790377,
   0.01573389683211943,
   0.012531325808456464],
  'brevity_penalty': 1.0,
  'length_ratio': 1.0839886149317888,
  'translation_length': 1004671,
  'reference_length': 926828})

In [25]:
np.mean(bs["precision"]), np.mean(bs["recall"]),np.mean(bs["f1"])

(0.6365280508995056, 0.5417277860014063, 0.5824678725317904)

In [ ]:
bleu.compute(predictions=predictions, max_order = 4, references=refs)

In [9]:

bleu.compute(predictions=predictions, max_order = 4, references=refs)

{'bleu': 0.034312445993591324,
 'precisions': [0.2048581077785663,
  0.03431786300790377,
  0.01573389683211943,
  0.012531325808456464],
 'brevity_penalty': 1.0,
 'length_ratio': 1.0839886149317888,
 'translation_length': 1004671,
 'reference_length': 926828}

In [21]:
import torch

max_length = model.config.n_positions
stride = 512

nlls = []
for i in range(0, 10):
    #print(i)
    input_text = dataset[i]["text"]  
    input_ids = tokenizer.encode(input_text, add_special_tokens=False, return_tensors="pt").to("cuda")
    #input_ids = torch.tensor([dataset[i]["input_ids"]]).to("cuda")
    #print(i, 1)
    input_ids = input_ids[:512]
    
    target_ids = input_ids.clone()
    target_ids[:, :] = -100

    with torch.no_grad():
        outputs = model(input_ids, labels=target_ids)
        neg_log_likelihood = outputs.loss * len(input_ids)
    #print(i, 2)

    nlls.append(neg_log_likelihood)
    print(i,neg_log_likelihood)

ppl = torch.exp(torch.stack(nlls).sum() / i)
ppl

0 tensor(nan, device='cuda:0')
1 tensor(nan, device='cuda:0')
2 tensor(nan, device='cuda:0')
3 tensor(nan, device='cuda:0')
4 tensor(nan, device='cuda:0')
5 tensor(nan, device='cuda:0')
6 tensor(nan, device='cuda:0')
7 tensor(nan, device='cuda:0')
8 tensor(nan, device='cuda:0')
9 tensor(nan, device='cuda:0')


tensor(nan, device='cuda:0')

In [35]:
len(dataset[19]["text"])

25806

In [52]:
dataset.select(range(10))["text"].shape

AttributeError: 'list' object has no attribute 'shape'

In [60]:
len(dataset.select(range(10))["text"])

10

In [8]:

token_list = []
for i in range(100):
    input_item = dataset[i]
    tensor = tokenizer.encode(input_item["text"], add_special_tokens=True, return_tensors="pt").to("cuda") 
    token_list.append(tensor)
encodings = torch.cat(token_list,1)
encodings.shape

torch.Size([1, 73096])

In [115]:
begin_loc = 100
seq_len = encodings.size(1)
end_loc = min(begin_loc + max_length, seq_len)
prev_end_loc = 0
trg_len = end_loc - prev_end_loc  # may be different from stride on last loop
input_ids = encodings[:, begin_loc:end_loc]
target_ids = input_ids.clone()
target_ids[:, :-trg_len] = -100
with torch.no_grad():
    outputs = model(input_ids, labels=target_ids)
outputs.loss, (encodings[:, begin_loc:end_loc].cpu().numpy())

(tensor(4.8928, device='cuda:0'),
 array([[11344,   359,   863, ...,  8721,   313,    12]], dtype=int64))

In [9]:
from tqdm import tqdm

max_length = model.config.n_positions
stride = 50

#input_text = dataset[i]["text"]  
#encodings = tokenizer.encode(input_text, add_special_tokens=False, return_tensors="pt").to("cuda")
#device = "cuda"
seq_len = encodings.size(1)

prev_end_loc = 0
count_sum = 0
nlls = []
pbar = tqdm(range(0, seq_len, stride))
for begin_loc in pbar:
    end_loc = min(begin_loc + max_length, seq_len)
    trg_len = end_loc - prev_end_loc  # may be different from stride on last loop
    input_ids = encodings[:, begin_loc:end_loc]
    target_ids = input_ids.clone()
    target_ids[:, :-trg_len] = -100

    with torch.no_grad():
        outputs = model(input_ids, labels=target_ids)

        # loss is calculated using CrossEntropyLoss which averages over input tokens.
        # Multiply it with trg_len to get the summation instead of average.
        # We will take average over all the tokens to get the true average
        # in the last step of this example.
        neg_log_likelihood = outputs.loss * trg_len

    nlls.append(neg_log_likelihood.cpu().numpy())

    prev_end_loc = end_loc
    pbar.set_postfix({"loss":(np.array(nlls[1:])/end_loc).sum()})
    if end_loc == seq_len:
        count_sum += end_loc
        break


#ppl = torch.exp((np.array(nlls)/end_loc).sum())
loss = (np.array(nlls[1:])/end_loc).sum()
(loss, np.exp(loss))

 97%|█████████▋| 1421/1462 [08:08<00:14,  2.91it/s, loss=6.57]


(6.566047787444524, 710.5560179623819)

In [123]:
(np.array(nlls[1:])/50).mean()

7.0311055

In [119]:
(loss, np.exp(loss))

(5.917751879220825, 371.5754277521345)

In [97]:
(np.array(nlls[1:])/end_loc).sum(), np.exp((np.array(nlls[1:])/end_loc).sum())

(3.0430849, 20.969833)

In [85]:
np.exp((np.array(nlls)/end_loc).sum())

349.2629

In [ ]:
torch.exp(torch.stack(nlls).sum() / end_loc),torch.exp(torch.stack(np.array(nlls)/end_loc).sum())

AttributeError: 'list' object has no attribute 'cpu'

In [46]:
count_sum

270

In [47]:
ppl = torch.exp(torch.stack(nlls).sum() / count_sum)
ppl

tensor(30.6271, device='cuda:0')

In [27]:
outputs.keys()
outputs.logits.shape

torch.Size([1, 125, 50000])

In [ ]:
inputs = tokenizer.encode(prompt, add_special_tokens=False, return_tensors="pt")
prompt_len = len(tokenizer.decode(inputs[0],skip_special_tokens=True, clean_up_tokenization_spaces=True))
outputs = model.generate(inputs, max_length=len(inputs[0])+50, do_sample=True, top_p=0.98, top_k=50)
tokenizer.decode(outputs[0])[prompt_len:].replace(" ##","").replace("<|endoftext|>","")

In [11]:
len(ids)//2

512

In [12]:
ids = dataset["test"].select(range(100))["input_ids"]

[]